In [26]:
import gffutils
import pysam
import unittest

In [35]:
def extract_gene_positions(gff_file):
    """
    Extracts the contig, start, and end positions of all genes from a GFF3 file.

    Args:
        gff_file (str): Path to the GFF3 file. The file must contain contig names, coding gene features (CDS), gene IDs, start, and end positions.

    Returns:
        dict: A dictionary where keys are gene IDs and values are dictionaries with contig names as keys and tuples of (start, end) positions as values.
    """
    # Create a database from the GFF3 file
    db = gffutils.create_db(gff_file, dbfn=':memory:', force=True, keep_order=True, merge_strategy='merge', sort_attribute_values=True)
    
    gene_positions = {}
    # Check if 'CDS' or 'gene' is in the features of the GFF file
    if not any(feature.featuretype in ['CDS', 'gene'] for feature in db.all_features()):
        raise ValueError("no CDS or gene in gff file")
    
    # Iterate over all genes in the database
    for gene in db.features_of_type(['CDS', 'gene']):
        gene_id = gene.id
        contig = gene.seqid
        start = gene.start
        end = gene.end
        if gene_id not in gene_positions:
            gene_positions[gene_id] = {}
        gene_positions[gene_id][contig] = (start, end)
    
    return gene_positions

def parse_vcf(vcf_file):
    """
    Parses a VCF file and creates a dictionary with keys as sites and values as dictionaries containing alleles for each sample.

    Args:
        vcf_file (str): Path to the VCF file (can also handle a .gz file).

    Returns:
        dict: A dictionary where keys are tuples of (chromosome, position) and values are dictionaries with sample names as keys and alleles as values. Allele (0,0) is homozygous reference, (0,1) is heterozygous, and (1,1) is also homozygous alternative.
    """
    vcf = pysam.VariantFile(vcf_file)
    site_dict = {}

    for record in vcf:
        # Create a snp id that concatenate chromosome, position, ref and alt alleles.
        site = str(record.chrom)+":"+str(record.pos)+":"+str(record.ref)+":"+str(record.alts[0])
        # Initalize the site in the dictionary
        site_dict[site] = {}
        # Iterate over all samples in the VCF file and add the alleles to the dictionary
        for sample in record.samples:
            alleles = record.samples[sample]['GT']
            site_dict[site][sample] = alleles

    return site_dict


In [37]:

# Example usage
gff_file = '/Users/linyusheng/MugGWAS/tests/test.gff'
gene_positions = extract_gene_positions(gff_file)
for gene_id, position in gene_positions.items():
    print(f"{gene_id}: {position}")

gene1: {'contig1': (100, 200)}
gene2: {'contig1': (300, 400)}
CDS1: {'contig2': (500, 600)}


In [25]:
# Example usage
vcf_file = '/Users/linyusheng/MugGWAS/data/snps.snp.filtered.vcf'
site_dict = parse_vcf(vcf_file)
for site, samples in site_dict.items():
    print(f"Site {site}:")
    for sample, alleles in samples.items():
        print(f"  Sample {sample}: Alleles {alleles}")

Site 26:83:A:G:
  Sample 6925_1#55: Alleles (1, 1)
  Sample 7001_2#12: Alleles (0, 0)
  Sample 7553_5#67: Alleles (1, 1)
  Sample 6925_2#76: Alleles (1, 1)
  Sample 7553_5#49: Alleles (0, 0)
  Sample 7622_5#91: Alleles (0, 0)
Site 26:483:G:A:
  Sample 6925_1#55: Alleles (1, 1)
  Sample 7001_2#12: Alleles (0, 0)
  Sample 7553_5#67: Alleles (1, 1)
  Sample 6925_2#76: Alleles (0, 0)
  Sample 7553_5#49: Alleles (0, 0)
  Sample 7622_5#91: Alleles (0, 0)
Site 26:869:C:T:
  Sample 6925_1#55: Alleles (1, 1)
  Sample 7001_2#12: Alleles (0, 0)
  Sample 7553_5#67: Alleles (1, 1)
  Sample 6925_2#76: Alleles (0, 0)
  Sample 7553_5#49: Alleles (0, 0)
  Sample 7622_5#91: Alleles (0, 0)
Site 26:2366:A:G:
  Sample 6925_1#55: Alleles (0, 0)
  Sample 7001_2#12: Alleles (0, 0)
  Sample 7553_5#67: Alleles (0, 0)
  Sample 6925_2#76: Alleles (1, 1)
  Sample 7553_5#49: Alleles (1, 1)
  Sample 7622_5#91: Alleles (0, 0)
Site 26:2966:G:A:
  Sample 6925_1#55: Alleles (1, 1)
  Sample 7001_2#12: Alleles (0, 0)
  Sa

In [29]:
len(gene_positions)

0